# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion) 

## Introduction: Business Problem <a name="introduction"></a># 

In this project we will try to find an optimal location for a Wine bar. Specifically, this report will be targeted to stakeholders interested in opening a **Wine Bar** in **Paris**, France.

We will try to detect **locations with low Wine Bar density**. We would also prefer animated area, we will looking for **locations close to existing other type of Bar**.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## 1- Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing Wine Bar in the neighborhood
* number of other Bars in the neighborhood

Following data sources will be needed to extract/generate the required information:
* We will use administrative Neighborhoods centers giving by **https://opendata.paris.fr**
* number of Wine Bar, other venues, and their type and location in every Arrondissement will be obtained using **Foursquare API**

### 1.1 Get Geo Data

Let collecting Geo Data with https://opendata.paris.fr

In [1]:
import pandas as pd
import numpy as np

In [2]:
url = "https://opendata.paris.fr/api/records/1.0/search/?dataset=quartier_paris&q=&rows=100&facet=l_qu&facet=c_ar"

df_Paris_Neigh = pd.read_json(url, orient='index')
df_Paris_Neigh = pd.DataFrame(df_Paris_Neigh.loc['records'][0])
df_Paris_Neigh = pd.DataFrame(pd.json_normalize(df_Paris_Neigh['fields']))
#Select only usefull data
df_Paris_Neigh = df_Paris_Neigh[['c_ar','l_qu','surface','geom_x_y', 'geom.coordinates']]
df_Paris_Neigh = df_Paris_Neigh.rename(columns={'c_ar':'Arrondissement','l_qu':'Neighborhood','surface':'Surface','geom_x_y':'Coordinates','geom.coordinates':'Polygon'})

print(df_Paris_Neigh.shape)
df_Paris_Neigh

(80, 5)


Arrondissement       Neighborhood       Surface  \
0               12      Quinze-Vingts  1.235916e+06   
1                3    Arts-et-Métiers  3.180877e+05   
2                3           Archives  3.677284e+05   
3                8  Faubourg-du-Roule  7.965891e+05   
4                6            Monnaie  2.933606e+05   
..             ...                ...           ...   
75              14    Petit-Montrouge  1.345774e+06   
76              19    Pont-de-Flandre  2.376238e+06   
77              16             Muette  5.477898e+06   
78              16           Chaillot  1.424035e+06   
79              17          Epinettes  1.378545e+06   

                            Coordinates  \
0        [48.8469159441, 2.37440162648]   
1        [48.8664702895, 2.35708313106]   
2        [48.8591924127, 2.36320505733]   
3        [48.8741355756, 2.30411880972]   
4        [48.8543844036, 2.34003537113]   
..                                  ...   
75       [48.8266526255, 2.32643699922]   
76       [48.8955557746, 2.38477722927]   
77        [48.8632745438, 2.2599358317]   
78  [48.8684336145, 2.2916790427400002]   
79       [48.8949426538, 2.32111874371]   

                                              Polygon  
0   [[[2.373204762234059, 48.84057029369178], [2.3...  
1   [[[2.360209979547445, 48.86519024025307], [2.3...  
2   [[[2.368479720528894, 48.85583081045625], [2.3...  
3   [[[2.311968475741771, 48.86992864646887], [2.3...  
4   [[[2.343168550439539, 48.85138855000365], [2.3...  
..                                                ...  
75  [[[2.329136731859957, 48.83412784173808], [2.3...  
76  [[[2.384878635968117, 48.88663051164197], [2.3...  
77  [[[2.245624861250342, 48.87635522218431], [2.2...  
78  [[[2.292681256210368, 48.86043711353505], [2.2...  
79  [[[2.325914214090841, 48.88853299519872], [2.3...  

[80 rows x 5 columns]

It looks perfect we have 80 Neighborhoods, their name surface, coordinates, and polygon for geojson.

### 1.2 Build Geojson

In order to visualise Neighborhoods in a map, we need a geojson of Paris.
We have all data needed, we just need to ordered it well !

In [3]:
geojson_paris = '{"type": "FeatureCollection", "features": ['
for i in range(df_Paris_Neigh.shape[0]):
    geojson_paris = geojson_paris + '{"type": "Feature", "properties": {"name": '  \
    + '"{}"'.format(df_Paris_Neigh.iloc[i]['Neighborhood']) \
    +  '}, "geometry": {"type": "Polygon", "coordinates": ' \
    + '{}'.format(df_Paris_Neigh.iloc[i]['Polygon']) \
    + '}, "id": ' \
    + '"{}"'.format(df_Paris_Neigh.iloc[i]['Neighborhood']) \
    + '}'
    
    if i != df_Paris_Neigh.shape[0]-1:
        geojson_paris = geojson_paris + ', '
    else:
        geojson_paris = geojson_paris + ']}'

geojson_paris

'{"type": "FeatureCollection", "features": [{"type": "Feature", "properties": {"name": "Quinze-Vingts"}, "geometry": {"type": "Polygon", "coordinates": [[[2.373204762234059, 48.84057029369178], [2.372414018728415, 48.84017111634058], [2.372120455208858, 48.84039422669529], [2.370575607294024, 48.84152814957792], [2.369181837918419, 48.842551117264144], [2.368462941018196, 48.84309366434974], [2.366029183881674, 48.84493028682856], [2.364836413709806, 48.84584371301591], [2.364433128355796, 48.84614003688701], [2.365366647494866, 48.84669546629608], [2.365378777673753, 48.8467026535563], [2.365483449334876, 48.84676503420254], [2.365485498206277, 48.84676620164319], [2.3655482151248313, 48.84680347987392], [2.365561424682992, 48.846811331168624], [2.365605988329807, 48.84683784941379], [2.365650419829159, 48.84686436873957], [2.3656822923691783, 48.84688332351592], [2.365685631295672, 48.846885308114125], [2.365694997291027, 48.84689087892888], [2.365941978828986, 48.84703776356267], [2

It looks well ! 

### 1.3 Get Venues Data

Now we need to request Foursquare to collect Paris Venues

In [4]:
#Foursquare credentials
CLIENT_ID = 'UP5SMBXQ1LN3OQCTMH423QPSUAQRZ5L2QTLLSY0QKDGFNAWN' # your Foursquare ID
CLIENT_SECRET = 'TCQRSW2DNSWQWJLPJQJAT2RX0QYFVJRKEZYEBBWOGTWHRFH3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: UP5SMBXQ1LN3OQCTMH423QPSUAQRZ5L2QTLLSY0QKDGFNAWN
CLIENT_SECRET:TCQRSW2DNSWQWJLPJQJAT2RX0QYFVJRKEZYEBBWOGTWHRFH3


In [5]:
#Get venues function
import requests # library to handle requests

def getNearbyVenues(names, lat_lon, radius=500):
    
    venues_list=[]
    for name, lat_lon in zip(names, lat_lon):
        
   
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat_lon[0], 
            lat_lon[1], 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat_lon[0], 
            lat_lon[1], 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [6]:
#Build Paris Venues
paris_venues = getNearbyVenues(names=df_Paris_Neigh['Neighborhood'], lat_lon=df_Paris_Neigh['Coordinates'])
#Check Result
print(paris_venues.shape)
paris_venues.head()

(5088, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Quinze-Vingts              48.846916                2.374402   
1  Quinze-Vingts              48.846916                2.374402   
2  Quinze-Vingts              48.846916                2.374402   
3  Quinze-Vingts              48.846916                2.374402   
4  Quinze-Vingts              48.846916                2.374402   

                                 Venue  Venue Latitude  Venue Longitude  \
0  Promenade plantée – La Coulée Verte       48.847632         2.375107   
1                          Les Embruns       48.847100         2.371883   
2                            Le Calbar       48.848702         2.375487   
3                      Viaduc des Arts       48.848664         2.372931   
4                   Le Pop-Up du Label       48.847497         2.375483   

  Venue Category  
0          Trail  
1       Creperie  
2   Cocktail Bar  
3         Bridge  
4            Bar

Nice, we have now 5088 venues but all categories are not usefull for us. Let's clean it !

We should select 'Wine Bar' of course but also all categories wich conatains 'Bar', 'Bistro', 'Pub'

In [7]:
#Check Venue type list
pd.set_option('display.max_rows', None)
paris_venues_check = paris_venues[['Venue Category','Venue']].groupby('Venue Category').count().sort_values(by=['Venue'], ascending=False)
paris_venues_check

Venue
Venue Category                        
French Restaurant                  681
Hotel                              401
Italian Restaurant                 185
Bakery                             166
Bar                                137
Japanese Restaurant                133
Café                               131
Plaza                              120
Bistro                             117
Coffee Shop                        100
Wine Bar                            91
Restaurant                          86
Cocktail Bar                        78
Pizza Place                         73
Sandwich Place                      61
Supermarket                         54
Burger Joint                        50
Park                                50
Bookstore                           48
Clothing Store                      47
Chinese Restaurant                  47
Pastry Shop                         44
Vietnamese Restaurant               43
Art Gallery                         43
Thai Restaurant                     43
Garden                              42
Ice Cream Shop                      39
Theater                             37
Asian Restaurant                    37
Creperie                            35
Seafood Restaurant                  35
Sushi Restaurant                    34
Tea Room                            34
Boutique                            33
Historic Site                       32
Korean Restaurant                   31
Vegetarian / Vegan Restaurant       30
Indian Restaurant                   30
Dessert Shop                        28
Cosmetics Shop                      28
Pedestrian Plaza                    27
Gym / Fitness Center                27
Cheese Shop                         27
Wine Shop                           26
Gourmet Shop                        26
Chocolate Shop                      25
Art Museum                          23
Tapas Restaurant                    23
Pub                                 23
Moroccan Restaurant                 21
Hotel Bar                           21
Indie Movie Theater                 21
Convenience Store                   21
Steakhouse                          21
Spa                                 20
Museum                              20
Salad Place                         20
Mexican Restaurant                  19
Fast Food Restaurant                19
Farmers Market                      19
Gastropub                           19
Beer Bar                            18
Diner                               18
Lebanese Restaurant                 18
Brasserie                           18
Grocery Store                       17
Shoe Store                          17
Women's Store                       17
Food & Drink Shop                   16
Concert Hall                        16
Department Store                    15
Pool                                15
Jewelry Store                       14
Deli / Bodega                       14
Gym                                 14
Furniture / Home Store              14
Men's Store                         13
Breakfast Spot                      13
Comedy Club                         13
Mediterranean Restaurant            12
Falafel Restaurant                  12
Bagel Shop                          12
Music Venue                         12
Arts & Crafts Store                 11
African Restaurant                  11
Miscellaneous Shop                  11
Liquor Store                        10
Greek Restaurant                    10
American Restaurant                 10
Beer Store                          10
Bus Stop                            10
Candy Store                         10
Perfume Shop                         9
Health Food Store                    9
Middle Eastern Restaurant            9
Science Museum                       9
Juice Bar                            9
Ethiopian Restaurant                 9
Tennis Court                         9
Electronics Store                    9
Toy / Game Store                     9
Lounge          

We should select 'Wine Bar' of course but also all categories wich conatains 'Bar', 'Bistro', 'Pub'

In [8]:
#paris_venues_search[paris_venues_search['Venue Category'].str.contains('Bar')]
paris_venues_check_limited = paris_venues_check.reset_index()
paris_venues_check_limited = paris_venues_check_limited[paris_venues_check_limited['Venue Category'].str.contains('Bar|Bistro|Pub')]
paris_venues_check_limited

Venue Category  Venue
4                   Bar    137
8                Bistro    117
10             Wine Bar     91
12         Cocktail Bar     78
48                  Pub     23
50            Hotel Bar     21
61             Beer Bar     18
96            Juice Bar      9
157             Gay Bar      4
168  Salon / Barbershop      3
214            Dive Bar      2
221          Hookah Bar      2
227         Karaoke Bar      2
253          Sports Bar      1
259           Irish Pub      1

Wait, Barbershop slipped in the list... Let remove it !

In [9]:
paris_venues_check_limited = paris_venues_check_limited.drop(index=168)
paris_venues_check_limited = paris_venues_check_limited.reset_index(drop=True)
paris_venues_check_limited

Venue Category  Venue
0             Bar    137
1          Bistro    117
2        Wine Bar     91
3    Cocktail Bar     78
4             Pub     23
5       Hotel Bar     21
6        Beer Bar     18
7       Juice Bar      9
8         Gay Bar      4
9        Dive Bar      2
10     Hookah Bar      2
11    Karaoke Bar      2
12     Sports Bar      1
13      Irish Pub      1

Ok, it looks great ! Let's filter Paris Venues List

In [10]:
#paris_venues_filtered = paris_venues[paris_venues['Venue Category'].str.contains('Bar|Bistro|Pub')]
list_venue = paris_venues_check_limited['Venue Category'].values.tolist()
paris_venues_filtered = paris_venues[paris_venues['Venue Category'].isin(list_venue)]
print(paris_venues_filtered.shape)
paris_venues_filtered.head()

(506, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
2   Quinze-Vingts              48.846916                2.374402   
4   Quinze-Vingts              48.846916                2.374402   
12  Quinze-Vingts              48.846916                2.374402   
16  Quinze-Vingts              48.846916                2.374402   
32  Quinze-Vingts              48.846916                2.374402   

                   Venue  Venue Latitude  Venue Longitude Venue Category  
2              Le Calbar       48.848702         2.375487   Cocktail Bar  
4     Le Pop-Up du Label       48.847497         2.375483            Bar  
12        Le Baron Rouge       48.849404         2.377445       Wine Bar  
16              Le China       48.849967         2.373779   Cocktail Bar  
32  CitizenM Rooftop bar       48.843573         2.371193      Hotel Bar

We don't really care about the Venue Category. We just want to count Wine Bar and others 'Night' Venues.
Let's create 2 columns for that :

In [11]:
paris_venues_filtered_count = paris_venues_filtered.copy()
paris_venues_filtered_count.insert(7, "Wine Bar", 0) 
paris_venues_filtered_count.insert(8, "Total Bar", 1) 
paris_venues_filtered_count.loc[paris_venues['Venue Category'] == 'Wine Bar', 'Wine Bar'] = 1

paris_venues_filtered_count

Neighborhood  Neighborhood Latitude  \
2                 Quinze-Vingts              48.846916   
4                 Quinze-Vingts              48.846916   
12                Quinze-Vingts              48.846916   
16                Quinze-Vingts              48.846916   
32                Quinze-Vingts              48.846916   
45                Quinze-Vingts              48.846916   
47                Quinze-Vingts              48.846916   
55                Quinze-Vingts              48.846916   
71                Quinze-Vingts              48.846916   
92              Arts-et-Métiers              48.866470   
93              Arts-et-Métiers              48.866470   
103             Arts-et-Métiers              48.866470   
117             Arts-et-Métiers              48.866470   
119             Arts-et-Métiers              48.866470   
123             Arts-et-Métiers              48.866470   
131             Arts-et-Métiers              48.866470   
134             Arts-et-Métiers              48.866470   
140             Arts-et-Métiers              48.866470   
141             Arts-et-Métiers              48.866470   
150             Arts-et-Métiers              48.866470   
154             Arts-et-Métiers              48.866470   
158             Arts-et-Métiers              48.866470   
164             Arts-et-Métiers              48.866470   
166             Arts-et-Métiers              48.866470   
172             Arts-et-Métiers              48.866470   
173             Arts-et-Métiers              48.866470   
187                    Archives              48.859192   
189                    Archives              48.859192   
193                    Archives              48.859192   
217                    Archives              48.859192   
225                    Archives              48.859192   
242                    Archives              48.859192   
246                    Archives              48.859192   
249                    Archives              48.859192   
259                    Archives              48.859192   
266                    Archives              48.859192   
269                    Archives              48.859192   
346           Faubourg-du-Roule              48.874136   
351                     Monnaie              48.854384   
355                     Monnaie              48.854384   
360                     Monnaie              48.854384   
366                     Monnaie              48.854384   
375                     Monnaie              48.854384   
378                     Monnaie              48.854384   
380                     Monnaie              48.854384   
385                     Monnaie              48.854384   
390                     Monnaie              48.854384   
393                     Monnaie              48.854384   
402                     Monnaie              48.854384   
423                     Monnaie              48.854384   
427                     Monnaie              48.854384   
430                     Monnaie              48.854384   
445                       Odéon              48.847801   
446                       Odéon              48.847801   
453                       Odéon              48.847801   
458                       Odéon              48.847801   
461                       Odéon              48.847801   
472                       Odéon              48.847801   
477                       Odéon              48.847801   
482                       Odéon              48.847801   
492                       Odéon              48.847801   
519              Champs-Elysées              48.867074   
529              Champs-Elysées              48.867074   
566              Champs-Elysées              48.867074   
593              Champs-Elysées              48.867074   
601              Maison-Blanche              48.823128   
604              Maison-Blanche              48.823128   
631                 Croulebarbe              48.833734   
641              

Now we will remove Venue Category Detail and group by Neighborhood

In [12]:
paris_venues_neigh = paris_venues_filtered_count[['Neighborhood','Wine Bar','Total Bar']].groupby('Neighborhood').sum().reset_index()
print(paris_venues_neigh.shape)
paris_venues_neigh

(75, 3)


Neighborhood  Wine Bar  Total Bar
0                    Amérique         0          1
1                    Archives         1         11
2                     Arsenal         1          5
3             Arts-et-Métiers         5         17
4                 Batignolles         1         12
5                  Belleville         1          9
6                       Bercy         2          6
7              Bonne-Nouvelle         5         18
8                    Chaillot         1          4
9              Champs-Elysées         0          4
10                   Charonne         0          2
11           Chaussée-d'Antin         0          3
12               Clignancourt         2         11
13                     Combat         1          2
14                Croulebarbe         0          4
15            Ecole-Militaire         0          1
16             Enfants-Rouges         5         13
17                  Epinettes         0          2
18                     Europe         1          5
19        Faubourg-Montmartre         2          9
20          Faubourg-du-Roule         0          1
21            Folie-Méricourt         4         21
22                    Gaillon         3          4
23                       Gare         0          2
24                Goutte-d'Or         1          5
25          Grandes-Carrières         1          8
26                   Grenelle         0          4
27               Gros-Caillou         0          7
28                     Halles         1          3
29        Hôpital-Saint-Louis         4         19
30                  Invalides         0          3
31         Jardin-des-Plantes         0          2
32                      Javel         0          2
33                La Chapelle         1          1
34                  Madeleine         0          3
35                       Mail         5         20
36             Maison-Blanche         0          2
37                    Monnaie         3         14
38               Montparnasse         0          9
39                     Necker         0          5
40                 Notre-Dame         3          6
41      Notre-Dame-des-Champs         1          8
42                      Odéon         1          9
43               Palais-Royal         3          4
44         Parc-de-Montsouris         0          1
45            Petit-Montrouge         0          2
46              Place-Vendôme         0          5
47         Plaine de Monceaux         0          7
48                  Plaisance         0          6
49            Pont-de-Flandre         0          3
50          Porte-Saint-Denis         1          9
51         Porte-Saint-Martin         1          5
52              Père-Lachaise         1          8
53              Quinze-Vingts         1          9
54               Rochechouart         2          5
55                   Roquette         1         20
56             Saint-Ambroise         1         16
57              Saint-Fargeau         0          1
58              Saint-Georges         1          9
59     Saint-Germain-des-Prés         4         10
60  Saint-Germain-l'Auxerrois         0          1
61              Saint-Gervais         3          7
62              Saint-Lambert         0          2
63                Saint-Merri         1          4
64       Saint-Thomas-d'Aquin         0          4
65               Saint-Victor         3         14
66      Saint-Vincent-de-Paul         0          1
67               Sainte-Avoie         2          8
68          Sainte-Marguerite         1          5
69                Salpêtrière         0          1
70                   Sorbonne         2          8
71                     Ternes         1          8
72               Val-de-Grâce         1          8
73                   Villette         0          9
74                   Vivienne         5          9

In [70]:
paris_venues_neigh[['Wine Bar','Total Bar']].agg(['sum', 'mean', 'min', 'max'])

Wine Bar   Total Bar
sum   91.000000  506.000000
mean   1.213333    6.746667
min    0.000000    1.000000
max    5.000000   21.000000

It looks very clear !

## 2- Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Paris that have **low Wine Bar density**. We would also prefer animated area, we will looking for locations **close to existing other type of Bar**.

In first step we have collected the required data: location and type (category) of every bar in Paris. We have also identified Wine Bar (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of **bar density** across different areas of Paris - we will use heatmaps to identify a few promising and focus our attention on those areas.


## 3- Analysis <a name="analysis"></a>

### 3.1 Visualise Bar Density

In [13]:
import folium # map rendering library
# create a plain world map
paris_all_bar_map = folium.Map(location=[ 48.8625627018, 2.33644336205], zoom_start=12)

# generate choropleth map
paris_all_bar_map.choropleth(
    geo_data=geojson_paris,
    data=paris_venues_neigh,
    columns=['Neighborhood', 'Total Bar'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Paris Bar Density'
)
    
# display map
paris_all_bar_map

Unfortunately Foium is not displayed in GitHub.
No problem, here is a picture of the result !

In [33]:
from PIL import Image
import requests
from io import BytesIO

response = requests.get('https://raw.githubusercontent.com/Phi-Cgl/Applied_Data_Science_Capstone/main/Paris%20Total%20Bar%20Density.png')
img = Image.open(BytesIO(response.content))
img

### 3.2 Compare it to Wine Bar Density

In [40]:
# create a plain world map
paris_wine_bar_map = folium.Map(location=[ 48.8625627018, 2.33644336205], zoom_start=12)

# generate choropleth map
paris_wine_bar_map.choropleth(
    geo_data=geojson_paris,
    data=paris_venues_neigh,
    columns=['Neighborhood', 'Wine Bar'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Paris Wine Bar Density'
)

# display map
paris_wine_bar_map

Same problem with folium, here is the picture for Wine Bar Density.

In [36]:
response = requests.get('https://raw.githubusercontent.com/Phi-Cgl/Applied_Data_Science_Capstone/main/Paris%20Wine%20Bar%20Density.png')
img = Image.open(BytesIO(response.content))
img

### 3.3 Create a unique KPI to visualise best place

It was very interesting to visualize Total Bar density and Wine Bar Density but it's not very easy to look at 2 maps.
We should limit Wine Bar density on High Total Wine Bar density.
Let filter panda dataframe on Total Wine Bar count above 14 and create a new ratio KPI.

In [52]:
paris_venues_neigh_high_bar_dens = paris_venues_neigh[paris_venues_neigh['Total Bar']>=14].copy() 
paris_venues_neigh_high_bar_dens['Ratio'] = paris_venues_neigh_high_bar_dens['Total Bar'] / paris_venues_neigh_high_bar_dens['Wine Bar']
paris_venues_neigh_high_bar_dens

Neighborhood  Wine Bar  Total Bar      Ratio
3       Arts-et-Métiers         5         17   3.400000
7        Bonne-Nouvelle         5         18   3.600000
21      Folie-Méricourt         4         21   5.250000
29  Hôpital-Saint-Louis         4         19   4.750000
35                 Mail         5         20   4.000000
37              Monnaie         3         14   4.666667
55             Roquette         1         20  20.000000
56       Saint-Ambroise         1         16  16.000000
65         Saint-Victor         3         14   4.666667

Perfect, and now, let's generate a new heatmap.

In [54]:
# create a plain world map
paris_wine_bar_limited_map = folium.Map(location=[ 48.8625627018, 2.33644336205], zoom_start=12)

# generate choropleth map
paris_wine_bar_limited_map.choropleth(
    geo_data=geojson_paris,
    data=paris_venues_neigh_high_bar_dens,
    columns=['Neighborhood', 'Ratio'],
    key_on='feature.properties.name',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Best Place for a wine Bar'
)

# display map
paris_wine_bar_limited_map

In [55]:
response = requests.get('https://raw.githubusercontent.com/Phi-Cgl/Applied_Data_Science_Capstone/main/Paris%20Wine%20Bar%20Best%20Place.png')
img = Image.open(BytesIO(response.content))
img

Great ! We clearly have 2 very intersting Neighborhood : Roquette and Saint Ambroise.

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of Bar in Paris : 506 Bar and Pub including 91 wine bar.
There is bar in all Neughborhood but they are concentrate in the city center.
Wine Bar after a first analysis looks concentrate in the same area.
By the way if we use ratio rather than number of Bar and number of wine Bar we can more easily check the best neighborhoods for a neq Wine bar !

Roquette and Saint Ambroise looks the best place to open a new Wine bar.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Paris areas with high number of Bar but low number of wine bar in order to aid stakeholders in narrowing down the search for optimal location for a wine bar. By calculating bar density distribution from Foursquare data we have first identified general boroughs that justify further analysis.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.